In [1]:
import torch
from torch.nn import functional as F
import torch.nn as nn
if torch.backends.mps.is_available():
    mps_device = torch.device("mps")
    x = torch.ones(1, device=mps_device)
    print(x)
    print("Running on MPS Device")
else:
    print("MPS device not found")

tensor([1.], device='mps:0')
Running on MPS Device


In [2]:
batch_size = 64
block_size = 256

max_iters = 5000
eval_iters = 200
eval_interval = 500
learning_rate = 3e-4
n_embed = 384
n_head = 6
n_layer = 6
dropout = 0.2

In [3]:
with open('data/shakespeare.txt', 'r', encoding='utf-8') as f:
    text = f.read()

In [4]:
chars = sorted(list(set(text)))
vocab_size = len(chars)
print(''.join(chars))
print(vocab_size)


 !$&',-.3:;?ABCDEFGHIJKLMNOPQRSTUVWXYZabcdefghijklmnopqrstuvwxyz
65


### Character level language model
### Encode characters to numbers

In [5]:
stoi = {ch: i for i, ch in enumerate(chars)}
itos = {i: ch for i, ch in enumerate(chars)}


# take a string output a list of integers
def encode(s): return [stoi[c] for c in s]
# decoder: take a list of integers, output a string
def decode(l): return ''.join([itos[i] for i in l])

In [6]:
print(encode("hii there"))
print(decode(encode("hii there")))
data = torch.tensor(encode(text), dtype=torch.long)
print(data.shape, data.dtype)
print(data[:100])

[46, 47, 47, 1, 58, 46, 43, 56, 43]
hii there
torch.Size([1115393]) torch.int64
tensor([18, 47, 56, 57, 58,  1, 15, 47, 58, 47, 64, 43, 52, 10,  0, 14, 43, 44,
        53, 56, 43,  1, 61, 43,  1, 54, 56, 53, 41, 43, 43, 42,  1, 39, 52, 63,
         1, 44, 59, 56, 58, 46, 43, 56,  6,  1, 46, 43, 39, 56,  1, 51, 43,  1,
        57, 54, 43, 39, 49,  8,  0,  0, 13, 50, 50, 10,  0, 31, 54, 43, 39, 49,
         6,  1, 57, 54, 43, 39, 49,  8,  0,  0, 18, 47, 56, 57, 58,  1, 15, 47,
        58, 47, 64, 43, 52, 10,  0, 37, 53, 59])


In [7]:
n = int(0.9 * len(data))
train_data = data[:n]
val_data = data[n:]
print(len(train_data), len(val_data))

1003853 111540


In [8]:
# block_size = 8
# train_data[: block_size+1]
# x = train_data[:block_size]
# y = train_data[1:block_size+1]
# for t in range(block_size):
#     context = x[:t+1]
#     target = y[t]
#     print(f"When input is {context}, output is {target}")

In [9]:
torch.manual_seed(1337)

def get_batches(split):
    # generate a small batch of data of inputs and targets y
    data = train_data if split == 'train' else val_data
    ix = torch.randint(len(data) - block_size, (batch_size,))
    x = torch.stack([data[i: i+block_size] for i in ix])
    y = torch.stack([data[i+1: i+block_size+1] for i in ix])
    x, y = x.to(mps_device), y.to(mps_device)
    return x, y



xb, yb = get_batches('train')
print("inputs:")
print(xb.shape)
print(xb)
print("targets:")
print(yb.shape)
print(yb)

print("---")

for b in range(batch_size):
    for t in range(block_size):
        context = xb[b, : t+1]
        target = yb[b, t]
        print(f"when input is {context.tolist()}, the target is: {target}")

inputs:
torch.Size([64, 256])
tensor([[ 1, 56, 53,  ..., 53, 51,  1],
        [10,  1, 39,  ..., 46, 43,  1],
        [50,  1, 58,  ..., 42,  1, 51],
        ...,
        [51, 43, 50,  ..., 43,  1, 46],
        [ 0, 35, 47,  ..., 54, 53, 47],
        [57, 59, 56,  ..., 45, 57,  1]], device='mps:0')
targets:
torch.Size([64, 256])
tensor([[56, 53, 63,  ..., 51,  1, 32],
        [ 1, 39,  1,  ..., 43,  1, 52],
        [ 1, 58, 43,  ...,  1, 51, 39],
        ...,
        [43, 50, 43,  ...,  1, 46, 43],
        [35, 47, 50,  ..., 53, 47, 50],
        [59, 56, 43,  ..., 57,  1, 53]], device='mps:0')
---
when input is [1], the target is: 56
when input is [1, 56], the target is: 53
when input is [1, 56, 53], the target is: 63
when input is [1, 56, 53, 63], the target is: 39
when input is [1, 56, 53, 63, 39], the target is: 50
when input is [1, 56, 53, 63, 39, 50], the target is: 58
when input is [1, 56, 53, 63, 39, 50, 58], the target is: 47
when input is [1, 56, 53, 63, 39, 50, 58, 47], the t

In [10]:
@torch.no_grad()
def estimate_loss():
    out = {}
    m.eval()
    for split in ['train', 'val']:
        losses = torch.zeros(eval_iters)
        for k in range(eval_iters):
            X, Y = get_batches(split)
            logits, loss = m(X, Y)
            losses[k] = loss.item()
        out[split] = losses.mean()
    m.train()
    return out

In [11]:
class Head(nn.Module):
  """ One head of self-attention"""

  def __init__(self, head_size):
    super().__init__()
    self.key = nn.Linear(n_embed, head_size, bias=False)
    self.query = nn.Linear(n_embed, head_size, bias=False)
    self.value = nn.Linear(n_embed, head_size, bias=False)
    self.register_buffer('tril', torch.tril(torch.ones(block_size, block_size)))
    self.dropout = nn.Dropout(dropout)


  def forward(self, x):
    B,T,C = x.shape
    k = self.key(x) #(B,T,C)
    q = self.query(x) #(B,T,C)
    # compute self-attention scores ("affinities")
    wei = q @ k.transpose(-2, -1) * C**-0.5 # shouldn't it be head_size instead of C?
    wei = wei.masked_fill(self.tril[:T, :T] == 0, float('-inf'))
    wei = F.softmax(wei, dim=-1) # (B,T,T)
    wei = self.dropout(wei)
    v = self.value(x)
    out = wei @ v
    return out

In [12]:
class MultiHeadAttention(nn.Module):
  """ multiple heads of self-attention"""

  def __init__(self, num_heads, head_size):
    super().__init__()
    self.heads = nn.ModuleList([Head(head_size) for _ in range(num_heads)])
    self.proj = nn.Linear(n_embed, n_embed)
    self.dropout = nn.Dropout(dropout)

  def forward(self, x):
    out = torch.cat([h(x) for h in self.heads], dim=-1)
    out = self.dropout(self.proj(out))
    return out

In [13]:
class FeedForward(nn.Module):
  """ a simple linear layer followed by a noon-linearity """

  def __init__(self, n_embed):
    super().__init__()
    self.net = nn.Sequential(
        nn.Linear(n_embed, 4*n_embed),
        nn.ReLU(),
        nn.Linear(4*n_embed, n_embed),
        nn.Dropout(dropout),
    )
  def forward(self, x):
    return self.net(x)

In [14]:
class Block(nn.Module):
  """ Transformer block: communication followed by computation """
  def __init__(self, n_embed, n_head):
    # n_embed: embedding dimention, n_head: the number of heads we'd like
    super().__init__() 
    head_size = n_embed // n_head
    self.sa = MultiHeadAttention(n_head, head_size)
    self.ffwd = FeedForward(n_embed)
    self.ln1 = nn.LayerNorm(n_embed)
    self.ln2 = nn.LayerNorm(n_embed)

  def forward(self, x):
    x = x + self.sa(self.ln1(x))
    x = x + self.ffwd(self.ln2(x))
    return x
  

In [15]:
class LayerNorm1d:
  def __init__(self, dim, eps=1e-5, momentum=0.1):
    
    self.eps = eps
    self.gamma = torch.ones(dim)
    self.beta = torch.zeros(dim)

    def __call__(self, x):
      # calculate the forward pass
      xmean = x.mean(1, keepdim=True) # batch mean
      xvar = x.var(1, keepdim=True) # batch variance
      xhat = (x - xmean) / torch.sqrt(xvar + self.eps)
      self.out = self.gamma * xhat + self.beta
      return self.out
    
    def parameters(self):
      return [self.gamma, self.beta]

In [16]:
torch.manual_seed(1337)

class BigramLanguageModel(nn.Module):

    def __init__(self):
        super().__init__()
        # number of embedding dimensions n_embed
        self.token_embedding_table = nn.Embedding(vocab_size, n_embed)
        self.position_embedding_table = nn.Embedding(block_size, n_embed)
        #self.sa_heads = MultiHeadAttention(4, n_embed//4) # i.e 4 heads of 8-dimentional self-attention
        #self.ffwd = FeedForward(n_embed)
        # self.blocks = nn.Sequential(
        #     Block(n_embed, n_head=4),
        #     Block(n_embed, n_head=4),
        #     Block(n_embed, n_head=4),
        #     nn.LayerNorm(n_embed),
        # )
        self.blocks = nn.Sequential(*[Block(n_embed, n_head=n_head) for _ in range(n_layer)])
        self.ln_f = nn.LayerNorm(n_embed)
        self.lm_head = nn.Linear(n_embed, vocab_size)  # Language modeling head

    def forward(self, idx, targets=None):
        B,T = idx.shape

        tok_emb = self.token_embedding_table(idx)  # (batch, time, channel)
        pos_emb = self.position_embedding_table(torch.arange(T, device=mps_device)) # (T, C)
        x = tok_emb + pos_emb # (B, T, C) , broadcasting along the Batch dimension, for pos_emb, a new batch dim is added
        #x = self.sa_heads(x)
        #x = self.ffwd(x)
        x = self.blocks(x)
        x = self.ln_f(x)
        logits = self.lm_head(x)  # (B,T,vocab_size) 

        if targets == None:
            loss = None
        else:
            B, T, C = logits.shape
            logits = logits.view(B*T, C)
            targets = targets.view(B*T)
            loss = F.cross_entropy(logits, targets)

        return logits, loss

    def generate(self, idx, max_new_tokens):
        # idx is (B,T)  array of indices in the current context

        for _ in range(max_new_tokens):
            idx_cond = idx[:, -block_size:]
            logits, loss = self(idx_cond)
            logits = logits[:, -1, :]
            probs = F.softmax(logits, dim=-1)
            idx_next = torch.multinomial(probs, num_samples=1)
            idx = torch.cat((idx, idx_next), dim=1)
        return idx

In [17]:
model = BigramLanguageModel()
m = model.to(mps_device)
logits, loss = m(xb, yb)
print(logits.shape)
print(loss)
context = torch.zeros((1, 1), dtype=torch.long, device=mps_device)
print(decode(m.generate(context, max_new_tokens=100)[0].tolist()))

torch.Size([16384, 65])
tensor(4.2846, device='mps:0', grad_fn=<NllLossBackward0>)

LcYj'EA-Fo?sjrpBSZlPuLwlBQs&cH
l.K3TEgXPlx
QT!WCs xSjZF.txl-BH peqEz-
DGb,-$.Blq&cHY:gdxbQ,CJq:bJo-.


In [18]:
optimizer = torch.optim.AdamW(m.parameters(), lr=1e-3)

In [19]:
for iter in range(max_iters):
    if iter % eval_interval == 0:
        losses = estimate_loss()
        print(
            f"step {iter}: train loss {losses['train']:.4f} val loss {losses['val']:.4f}")

    xb, yb = get_batches('train')
    logits, loss = m(xb, yb)
    optimizer.zero_grad(set_to_none=True)
    loss.backward()
    optimizer.step()

step 0: train loss 4.2849 val loss 4.2827
step 500: train loss 1.6576 val loss 1.8145
step 1000: train loss 1.3470 val loss 1.5630
step 1500: train loss 1.2300 val loss 1.5051
step 2000: train loss 1.1539 val loss 1.4844
step 2500: train loss 1.0886 val loss 1.4883
step 3000: train loss 1.0302 val loss 1.5014
step 3500: train loss 0.9678 val loss 1.5123
step 4000: train loss 0.9094 val loss 1.5534
step 4500: train loss 0.8565 val loss 1.5883


In [25]:
context = torch.zeros((1, 1), dtype=torch.long, device=mps_device)
print(decode(m.generate(idx=context, max_new_tokens=50)[0].tolist()))


SOMERSET:
In brief that our counsel shall not ther


In [26]:
torch.save(m.state_dict(), './saved_models/multiheaded_attention.pth')

In [27]:
model2 = BigramLanguageModel()
model2.load_state_dict(torch.load('./saved_models/multiheaded_attention.pth'))

<All keys matched successfully>

In [ ]:
model2.inference(50)